# LQR design for cart pole systems 

In this notebook we demonstrate on using [Drake](https://drake.mit.edu/) to synthesize linear quadratic 
regulators (LQR) for cart pole systems. First we linearize by hand and compare with 
linearization from Drake, then perform balancing with LQR for a few initial states.
Later we learn how to define cart poles using 
[Unified Robot Description Format (URDF)](https://wiki.ros.org/urdf). 

**Note :** The contents in this notebook follows [ [1](https://underactuated.csail.mit.edu/) ] closely, with links to certain sections of the 
[Underactuated Robotics book](https://underactuated.csail.mit.edu/index.html). I couldn't find any other way 
to learn Drake efficiently without such superb materials. However, even though some problem sets here look similar 
to some exercises on that book, I have modified them somehow so that using code from here would fail 
the autograder in the original notebook for a particular exercise.  

### Cart-pole dynamics

I believe we are all familiar with a cart-pole, sometime called invert pendulum, shown in Figure 1 The control 
objective is to balance the pendulum around its upright position; i.e., unstable equilibrium, using only horizontal 
force on the cart.  Refer to 
[Section 3.2 of Underactuated Robotics](https://underactuated.csail.mit.edu/acrobot.html#cart_pole) 
for analysis of cart-pole nonlinear dynamics.
<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/cart_pole.png" width=500 />
</div>
<div align="center">Figure 1 a 2D cart pole system</div>

First import required packages.

**Note :** In addition to Drake, you need to install underactuated package if haven't done so. 

```python
!pip install underactuated
```

In [1]:
import numpy as np
from IPython.display import HTML, display
from pydrake.all import (
    AddMultibodyPlantSceneGraph,
    DiagramBuilder,
    Linearize,
    LinearQuadraticRegulator,
    Parser,
    PlanarSceneGraphVisualizer,
    Simulator,
)

from underactuated import ConfigureParser

For simplicity, let's substitute

- mass of the cart $m_{\text{c}}=1$,
- mass of the pole $m_{\text{p}}=1$,
- length of the pole $l=1$,
- gravity acceleration $g=9.81$.

The cart pole state is defined as $\mathbf{x} = [x, \theta, \dot{x}, \dot{\theta}]^T$, and 
the force on the cart is the control input $\mathbf{u} = [f_x]$.

Use [equations (16) and (17)](https://underactuated.csail.mit.edu/acrobot.html#cart_pole) from the textbook for the accelerations:

$$\ddot{x} = \frac{1}{m_c + m_p \sin^2\theta}[ f_x+m_p \sin\theta (l \dot\theta^2 + g\cos\theta)] \tag{16}$$

$$\ddot{\theta} = \frac{1}{l(m_c + m_p \sin^2\theta)}[ -f_x \cos\theta - m_p l \dot\theta^2 \cos\theta \sin\theta - (m_c + m_p) g \sin\theta] \tag{17}$$

Implement the 
vector $\dot{\mathbf{x}} = [\dot{x}, \dot{\theta}, \ddot{x}, \ddot{\theta}]^T$ as $\dot{\mathbf{x}} = {\bf f}(\mathbf{x}, \mathbf{u})$. 
in the function ${\bf f}$ below to return $\dot{\mathbf{x}}$.


In [2]:
# function that given the cart-pole state x (4d array)
# and the input u (1d array) returns the right
# hand side of the state space dynamics h(x,u)
# (remember that we fixed the cart-pole parameters
# to the values above!)
def f(x, u):
    c = np.cos(x[1])  # cos(theta)
    s = np.sin(x[1])  # sin(theta)
    # parameters
    m_c = 1.0  # cart mass
    m_p = 1.0  # pendulum mass
    l = 1.0  # pole length
    g = 9.81  # gravity

    f1 = x[2]  # x_dot is the 3rd element of state vector
    f2 = x[3]  # theta_dot is the 4th element of state vector
    f3 = (1/(m_c + m_p*s**2))*(u[0] + m_p*s*(l*x[3]**2+g*c))  # from (16)
    f4 = (1/(l*(m_c + m_p*s**2)))*(-u[0]*c - m_p*l*x[3]**2*c*s - (m_c+m_p)*g*s)  # from (17)

    return np.array([f1, f2, f3, f4])

### Linearized around unstable equilibrium

Consider the unstable equilibrium state $$\mathbf{x}^* = [0, \pi, 0, 0]^T,$$ with the related equilibrium control 
input $$\mathbf{u}^* = [0].$$
Use the method provided in [the Underactuated book](https://underactuated.csail.mit.edu/acrobot.html#linearizing_manip)
to derive a linear model in the form
$$\dot{\bar{\mathbf{x}}} = A_{\text{lin}} \mathbf{\bar{x}} + B_{\text{lin}} \mathbf{\bar{u}},$$
where $\mathbf{\bar{x}} = \mathbf{x}-\mathbf{x}^*$ and $\mathbf{\bar{u}} = \mathbf{u} -\mathbf{u}^*$.

The derivation detail is shown in Figure 2
<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/cardpole_linearize.png" width=600 />
</div>
<div align="center">
Figure 2 Linearization detail of the cart-pole
</div>
Write functions to return the linear matrix/vector $A_{\text{lin}}$ and $B_{\text{lin}}$, according to the handwriting above.


In [3]:
def get_A_lin():
    g = 9.81  # gravity
    A = np.array(
        [
            [0, 0, 1, 0],  
            [0, 0, 0, 1],  
            [0, g, 0, 0], 
            [0, 2*g, 0, 0],  
        ]
    )
    return A

def get_B_lin():
    B = np.array(
        [
            [0],
            [0],
            [1],
            [1],
        ]  
    )
    return B

## Linearization Error
The linear model we have built above is accurate around the equilibrium point, but error would increse when
our state is farther away from the equilibrium.

The following function, for a given state $\mathbf{x}$ and control $\mathbf{u}$, evaluates the linearization error:
$$e(\mathbf{x}, \mathbf{u}) = \| {\bf f}(\mathbf{x}, \mathbf{u}) - {\bf f_{\text{lin}}}(\mathbf{x}, \mathbf{u}) \|$$
where we defined ${\bf f_{\text{lin}}}(\mathbf{x}, \mathbf{u}) = A_{\text{lin}} \mathbf{\bar{x}} + B_{\text{lin}} \mathbf{\bar{u}}.$

In [4]:
def f_lin(x, u):
    # equilibrium point
    x_star = np.array([0, np.pi, 0, 0])
    u_star = np.array([0])

    # linearized dynamics
    x_bar = x - x_star
    u_bar = u - u_star
    A = get_A_lin()
    B = get_B_lin()

    return A.dot(x_bar) + B.dot(u_bar)


def linearization_error(x, u):
    return np.linalg.norm(f(x, u) - f_lin(x, u))

Use the function above to evaluate the error $e(\mathbf{x}, \mathbf{u})$ in the following 6 conditions. 
(Feel free to change these and observe the errors and balancing results later on.)
- $\mathbf{x} = [0, 0.99 \pi, 0, 0]^T$ and $\mathbf{u} = [1]$,
- $\mathbf{x} = [0, 0.9 \pi, 0, 0]^T$ and $\mathbf{u} = [-10]$,
- $\mathbf{x} = [-1, 0.85 \pi, 0, 0]^T$ and $\mathbf{u} = [0]$,
- $\mathbf{x} = [0, 0.7 \pi, 0, 0]^T$ and $\mathbf{u} = [0]$,
- $\mathbf{x} = [0, 0.5 \pi, 0, 0]^T$ and $\mathbf{u} = [0]$,
- $\mathbf{x} = [1, \pi, 0, 0]^T$ and $\mathbf{u} = [10]$,


In [5]:
x_list = [
    np.array([0, 0.99*np.pi, 0, 0]),  
    np.array([0, 0.9*np.pi, 0, 0]),  
    np.array([-1, 0.85*np.pi, 0, 0]),  
    np.array([0, 0.7*np.pi, 0, 0]), 
    np.array([0, 0.5*np.pi, 0, 0]),  
    np.array([1, np.pi, 0, 0]),  
]

# fill these inputs with the ones given above
u_list = [
    np.array([1]),  # modify here
    np.array([-10]),  # modify here
    np.array([0]),  # modify here
    np.array([0]),  # modify here
    np.array([0]),  # modify here
    np.array([10]),  # modify here
]

# compute linearization errors for all the points above
errors = [linearization_error(x_list[i], u_list[i]) for i in range(6)]

Below we compare these linearization errors with the norm of $\dot{\mathbf{x}}$, i.e.,
$
\| {\bf f}(\mathbf{x}, \mathbf{u})\|$

Clearly, the smaller the linearization error with respect to this value, the better is our linear model.

Spend some time to convince yourself about this result.
Try to answer the following questions:
- Is our linear approximation valid for all the points we tested?
- Do we expect a linear controller to do a decent job when $\theta = \pi/2$?
- When $\theta$ is different from zero, does the linearization error depend on $\mathbf{u}$?
- What about the position $x$ of the cart? Should it affect the linearization error? If no, why not?


In [6]:
for i, e in enumerate(errors):
    print(f"State = {np.around(x_list[i], decimals=3)}^T")
    print(f"Input = {np.around(u_list[i], decimals=3)}")
    print("Linearization error = {:.3f}".format(e))
    print("Norm of f(x,u) = {:.3f}\n".format(np.linalg.norm(f(x_list[i], u_list[i]))))

State = [0.   3.11 0.   0.  ]^T
Input = [1]
Linearization error = 0.001
Norm of f(x,u) = 0.790

State = [0.    2.827 0.    0.   ]^T
Input = [-10]
Linearization error = 2.354
Norm of f(x,u) = 18.450

State = [-1.    2.67  0.    0.  ]^T
Input = [0]
Linearization error = 2.289
Norm of f(x,u) = 8.085

State = [0.    2.199 0.    0.   ]^T
Input = [0]
Linearization error = 10.976
Norm of f(x,u) = 9.999

State = [0.    1.571 0.    0.   ]^T
Input = [0]
Linearization error = 26.054
Norm of f(x,u) = 9.810

State = [1.    3.142 0.    0.   ]^T
Input = [10]
Linearization error = 0.000
Norm of f(x,u) = 14.142



## Design LQR controller to balance the cart-pole

Linearization by hand does not cause much suffering for a simple system such as cart-pole. One should do it at least once for 
better understanding of the basics.

For more complicated ystems, Drake could perform linearization transparently. 
So we will use that software feature for [LQR controller design](https://underactuated.csail.mit.edu/lqr.html). 

Define the state vector for unstable equilibrium point

In [7]:
x_star = [0, np.pi, 0, 0]

and the weight matrices for LQR controller. Adjust them as you wish, as long as 
$Q \ge 0$ (positive semidefinite) and $R \gt 0$ (positive definite). Note that adjusting both "knobs" in the same direction 
does not affect the optimization much. They should be penalized against each other. For example, increasing $R$ should result in 
less controller effort. 

In [8]:
Q = np.eye(4)
R = np.eye(1)

Then we construct the block diagram with the cart-pole in closed loop with the LQR controller.

In [9]:
# start construction site of our block diagram
builder = DiagramBuilder()

# instantiate the cart-pole and the scene graph
cartpole, scene_graph = AddMultibodyPlantSceneGraph(builder, time_step=0.0)
parser = Parser(cartpole)
ConfigureParser(parser)
parser.AddModelsFromUrl("package://underactuated/models/undamped_cartpole.urdf")
cartpole.Finalize()

# set the operating point (vertical unstable equilibrium)
context = cartpole.CreateDefaultContext()
context.get_mutable_continuous_state_vector().SetFromVector(x_star)

# fix the input port to zero and get its index for the lqr function
cartpole.get_actuation_input_port().FixValue(context, [0])
input_i = cartpole.get_actuation_input_port().get_index()

# synthesize lqr controller directly from
# the nonlinear system and the operating point
lqr = LinearQuadraticRegulator(cartpole, context, Q, R, input_port_index=input_i)
lqr = builder.AddSystem(lqr)

# the following two lines are not needed here...
output_i = cartpole.get_state_output_port().get_index()
cartpole_lin = Linearize(
    cartpole, context, input_port_index=input_i, output_port_index=output_i
)

# wire cart-pole and lqr
builder.Connect(cartpole.get_state_output_port(), lqr.get_input_port(0))
builder.Connect(lqr.get_output_port(0), cartpole.get_actuation_input_port())

# add a visualizer and wire it
visualizer = builder.AddSystem(
    PlanarSceneGraphVisualizer(
        scene_graph, xlim=[-3.0, 3.0], ylim=[-1.2, 1.2], show=False
    )
)
builder.Connect(scene_graph.get_query_output_port(), visualizer.get_input_port(0))

# finish building the block diagram
diagram = builder.Build()

# instantiate a simulator
simulator = Simulator(diagram)
simulator.set_publish_every_time_step(False)  # makes sim faster

**Aside :** At this point Drake, using Linearize(), spits out a linearized system cartpole_lin for us. You could compare your 
hand derivation above with cartpole_lin.A() and cartpole_lin.B() to verify whether they match.

In [10]:
print("A matrix from Drake")
print(cartpole_lin.A())
print("A matrix from your derivation")
print(get_B_lin())
print("B vector from Drake")
print(cartpole_lin.B())
print("B vector from your derivation")
print(get_B_lin())

A matrix from Drake
[[ 0.    0.    1.    0.  ]
 [ 0.    0.    0.    1.  ]
 [ 0.    9.81  0.    0.  ]
 [ 0.   19.62  0.    0.  ]]
A matrix from your derivation
[[0]
 [0]
 [1]
 [1]]
B vector from Drake
[[0.]
 [0.]
 [1.]
 [1.]]
B vector from your derivation
[[0]
 [0]
 [1]
 [1]]


The following cell contains a function that simulates the closed-loop system 
and produces a video of the simulation.

In [11]:
# function that given the cart-pole initial state
# and the simulation time, simulates the system
# and produces a video

def simulate_and_animate(x0, sim_time=5):
    # start recording the video for the animation of the simulation
    visualizer.start_recording()

    # reset initial time and state
    context = simulator.get_mutable_context()
    context.SetTime(0.0)
    context.SetContinuousState(x0)

    # run sim
    simulator.Initialize()
    simulator.AdvanceTo(sim_time)

    # stop video
    visualizer.stop_recording()

    # construct animation
    ani = visualizer.get_recording_as_animation()

    # display animation below the cell
    display(HTML(ani.to_jshtml()))

    # reset to empty video
    visualizer.reset_recording()

Run this function for all initial states created in x_list and observe the results.

In [12]:
# simulate and animate the cart
for x in x_list:
    simulate_and_animate(x)

Out of the 6 initial states we considered, which are the states from which the LQR controller is able to recover?

## Create cart-poles using URDF

In [14]:
# packages used for the second part
import numpy as np
from pydrake.all import (
    AddMultibodyPlantSceneGraph,
    DiagramBuilder,
    LinearQuadraticRegulator,
    MeshcatVisualizer,
    ModelVisualizer,
    Parser,
    Simulator,
    StartMeshcat,
)

from underactuated import running_as_notebook

In [15]:
# Start the visualizer (run this cell only once, each instance consumes a port)
meshcat = StartMeshcat()

INFO:drake:Meshcat listening for connections at http://localhost:7000


Now we move on to the second part of this notebook. The objectives are

- writing URDF to create single and double pendulum cart-pole systems
- synthesize LQR controllers for the single and double pendulum cart-poles

URDF (Unified Robot Description Format) is one of the most widely used formats to describe the geometry of robots. 
They are represented in XML and can be stored in strings as we will do later. In this 
problem, we will build a  single pendulum cartpole described in 
[Section 3.2](http://underactuated.csail.mit.edu/acrobot.html#cart_pole) 
of the textbook as a base to understand the construction of a basic URDF, then 
modify the system into a double pendulum cartpole. 
We will then wire up LQR controllers and simulate the cart-poles.

**Note**: For the sake of this problem, we consider x to be the horizontal direction and z to be the vertical direction. 

The single pendulum cart-pole system that we are using for learning URDF is the same as in Figure 1. We simplify 
by omitting parameters and attach a coordinate frame 
as shown in Figure 2 below. Note from the right-hand rule that the Y-axis should point into the page.
              
<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/cart_pole_wframe.png" width=500 />
</div>
<div align="center">
Figure 2 single pendulum cart pole with coordnate frame
</div>
### URDFs

The simple URDFs used in this example consist of three major components:

1.  **Links**: inertial and visual information for each link
2.  **Joints**: the connection between links
3.  **Transmissions**: control inputs to joints

We will go over each of these three in detail next.

Referring to 
[cartpole.urdf](https://github.com/RussTedrake/underactuated/blob/master/underactuated/models/cartpole.urdf) 
(used in textbook examples) can be helpful.

### Links
A link component here has three parts: the name (used to identify the link), the inertial (used to define the mass and  
center of mass of the link, and other dynamical properties such as inertia), and the visual (used for displaying 
representative images, but does not affect the system dynamics). 

Another component often used in urdfs is the collision geometry, which is not discussed here. 
You can refer to http://wiki.ros.org/urdf/XML/link for more details.

#### 1. Base Link
    
Below you will find the first link, which will represent the base cart. Note the three components from before: 
(1) the link name ("base"), (2) the inertial, with COM at (0, 0, 0.25) and mass of 1, and (3) the visuals, consisting 
of a box for the body of the cart and two spheres for the wheels with their positions set relative to the link's origin. 

**Note :** 
1. The offset of 0.25 in the Z direction is added to lift the cart origin above ground.
2. Inertia tags are coded for completeness only. They are not needed in this simple system.


In [16]:
base_urdf = """
  <link name="base">

    <inertial>
      <origin xyz="0 0 0.25" />
      <mass value="1" />
      <inertia ixx="0" ixy="0" ixz="0" iyy="0" iyz="0" izz="0" />
    </inertial>

    <visual>
      <origin xyz="0 0 0.25" />
      <geometry>
        <box size=".6 .3 .3" />
      </geometry>
      <material>
        <color rgba="0 1 0 1" />
      </material>
    </visual>

    <visual>
      <origin xyz=".15 0 0.025" rpy="0 0 0" />
      <geometry>
        <sphere radius=".05" />
      </geometry>
      <material>
        <color rgba="0 0 0 1" />
      </material>
    </visual>
    
    <visual>
      <origin xyz="-.15 0 0.025" rpy="0 0 0" />
      <geometry>
        <sphere radius=".05" />
      </geometry>
      <material>
        <color rgba="0 0 0 1" />
      </material>
    </visual>
  </link>
"""

#### 2. Pendulum Link
Next we have the pendulum link. The pendulum is defined by a ball mass and a cylinder rod where the COM is at the ball mass. 

In the next cell, complete the description for a pendulum that has a 5 cm radius spherical ball with mass 1 kg and a 1 m 
cylindrical rod of radius 1 cm. 

In [17]:
pendulum_link = """ 
  <link name="pendulum0">
    
  <!-- This is how you can write comments in urdfs -->
  <!-- TODO: Write the inertial component below -->
    <inertial>
      <origin xyz="0 0 -1.0" rpy="0 0 0" />
      <mass value="1" />
      <inertia ixx="0" ixy="0" ixz="0" iyy="0" iyz="0" izz="0" />
    </inertial>

  <!-- TODO: Write the visual component for the sphere (radius=0.05, mass=1.) below -->
    <visual>
        <origin xyz = "0 0 -1.0" rpy = "0 0 0" />
        <geometry>
            <sphere radius="0.05" />
        </geometry>
     <material>
        <color rgba="0 0 1.0 1" />
      </material>
    </visual>

  <!-- TODO: Write the visual component for the cylindrical rod (radius=0.01, length=1.) below -->
    <visual>
        <origin xyz = "0 0 -0.5" rpy = "0 0 0" />
        <geometry>
            <cylinder radius="0.01" length="1.0" />
        </geometry>
     <material>
        <color rgba="1.0 0 0 1" />
      </material>
    </visual>
  </link>
"""

### Joints

Now we move onto joints, which are used to connect links and define their behavior. Every joint has a unique name and a type 
specified. Of the various type of joints, we will be using two: **prismatic** and **continuous**. You can refer 
to http://wiki.ros.org/urdf/XML/joint for information on the joint types available and other elements in the joints description.

#### 1. Base Joint
    
The first joint we must consider is how the cart fits into the world, which is the root parent of our cart-pole system. 
Here we treat this as a sliding or prismatic joint as if the cart is moving on a fixed track in the x direction. 
Observe how all this information is contained in the joint description below. The `axis` element of a joint depends on 
the type of the joint; for prismatic joint, it is the axis of translation, in the joint's frame.


In [18]:
base_joint = """
  <joint name="x" type="prismatic">
    <parent link="world" />
    <child link="base" />
    <origin xyz="0 0 0" />
    <axis xyz="1 0 0" />
  </joint>
"""

#### 2. Pendulum Joint

The second joint to consider is for pendulum links connected to the cart base. We will treat these as continuous joints 
allowing them to revolve around their parent origin. Be careful about the axis of rotation: in this example, Y-axis 
is going into the page but $\theta$ points along $[0, -1, 0]$ by the right hand rule (curl your fingers in positive $\theta$, 
the direction of the thumb is the direction of theta).

In [19]:
pendulum_joint = """
<!-- TODO: write the parent, child, axis and origin for the pendulum joint named "theta0" with type "continuous". -->
    <joint name="theta0" type="continuous">
        <parent link="base" />
        <child link="pendulum0" />
        <origin xyz="0 0 0.25" />
        <axis xyz="0 -1 0" />
    </joint>
"""

### Transmissions

Lastly, we come to the transmission component. Here the only controlled input is a force applied in the x direction 
on the cart base. 

In [20]:
transmission = """
  <transmission type="SimpleTransmission" name="base_force">
    <actuator name="force" />
    <joint name="x" />
  </transmission>
"""

## Assembling the URDF

Now we have all the components necessary to construct a URDF for the cart-pole. Below is a function that assembles 
these components and adds a header and an ender to wrap them into one system. Take a few minutes to see how the 
generated urdf looks like.

In [21]:
single_pendulum_urdf = f"""
<?xml version="1.0"?><robot name="OurCartPole">
{base_urdf}
{pendulum_link}
{base_joint}
{pendulum_joint}
{transmission}
  </robot>
</xml>
"""
print(single_pendulum_urdf)


<?xml version="1.0"?><robot name="OurCartPole">

  <link name="base">

    <inertial>
      <origin xyz="0 0 0.25" />
      <mass value="1" />
    </inertial>

    <visual>
      <origin xyz="0 0 0.25" />
      <geometry>
        <box size=".6 .3 .3" />
      </geometry>
      <material>
        <color rgba="0 1 0 1" />
      </material>
    </visual>

    <visual>
      <origin xyz=".15 0 0.025" rpy="0 0 0" />
      <geometry>
        <sphere radius=".05" />
      </geometry>
      <material>
        <color rgba="0 0 0 1" />
      </material>
    </visual>
    
    <visual>
      <origin xyz="-.15 0 0.025" rpy="0 0 0" />
      <geometry>
        <sphere radius=".05" />
      </geometry>
      <material>
        <color rgba="0 0 0 1" />
      </material>
    </visual>
  </link>

 
  <link name="pendulum0">
    
  <!-- This is how you can write comments in urdfs -->
  <!-- TODO: Write the inertial component below -->
    <inertial>
      <origin xyz="0 0 -1.0" rpy="0 0 0" />
      <mas

## Visualizing the Cartpole URDF
Let us now visualize the generated urdf using `ModelVisualizer`. Make sure that, with $x = 0$ and $\theta_0 = 0$, 
the cart-pole should be in the configuration as shown in Figure 3. 
<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/single_cart_pole_initial.png" width=600 />
</div>
<div align="center">
Figure 3 single pendulum cart pole at rest
</div>

Using the controls that appear in the top right 
corner of the Meshcat window, change the values of $x$ and $\theta_0$ to see the cartpole in different configurations. 

In [22]:
visualizer = ModelVisualizer(meshcat=meshcat)
visualizer.parser().AddModelsFromString(single_pendulum_urdf, "urdf")
visualizer.Run(loop_once=not running_as_notebook)
meshcat.Delete()
meshcat.DeleteAddedControls()

INFO:drake:Click 'Stop Running' or press Esc to quit


What is the state at the unstable equilibrium for the single-pendulum cart-pole (when the pendulum is standing upright)?

**Note**: The state here is defined by $[x, \theta_0, \dot{x}, \dot{\theta}_0]$

In [29]:
x_star_single_pendulum = [0, np.pi, 0, 0]

## Double Pendulum URDF

Now that we've managed to create the URDF for the single pendulum cart-pole, we have all the tools to make a multi-pendulum 
cart-pole.  

The crucial point to note is the frame used to define links and joints: in the **child** link, all the origins of inertial 
and visual elements are defined wrt to the **joint** frame, and the **joint origin** is defined wrt to the frame of the 
**parent** link. The figure [here](http://wiki.ros.org/urdf/XML/joint) can be useful for understanding this point. 

For example, In the single pendulum case, the base-pendulum joint was the same as the parent (base) origin, and the
pendulum's home state $\theta = 0$ was defined wrt to the joint (the origin). 

For the case of the double pendulum cart-pole, first think about where the pendulum$0$-pendulum$1$ joint will be located 
(in the frame of pendulum0). Then in the frame of this joint, think about how the second pendulum (pendulum1) will be 
situated for the $\theta_1=0$ configuration. Figure 4 below show how $\theta_0$ and $\theta_1$ are defined. 

<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/double_cart_pole_angledef.png" width=500 />
</div>
<div align="center">
Figure 4 : definition of $\theta_0$ and $\theta_1$
</div>

**Note :** here $\theta_1$ is defined differently from 
[Exercise 3.2 of the underactuated book](https://underactuated.csail.mit.edu/acrobot.html#section8)

In the next cell, define the second pendulum (with same inertial and visual properties as the first pendulum), and the 
joint connecting the first and the second pendulum. Assemble the components for the double-pendulum cart-pole: 
concatenate the strings and add header and ender to generate the urdf. 

In [23]:
second_pendulum_joint = """
  <joint name="theta1" type="continuous">

    <!-- TODO: Complete the joint description -->
        <parent link="pendulum0" />
        <child link="pendulum1" />
        <axis xyz="0 -1 0" />
        <origin xyz="0 0 -1" rpy="0 0 0" />

  </joint>
"""

second_pendulum_link = """
  <link name="pendulum1">

    <!-- TODO: Complete the link description -->
    <inertial>
      <origin xyz="0 0 1.0" rpy="0 0 0" />
      <mass value="1" />
    </inertial>


  <!-- TODO: Write the visual component for the sphere (radius=0.05, mass=1.) below -->
    <visual>
        <origin xyz = "0 0 -1.0" rpy = "0 0 0" />
        <geometry>
            <sphere radius="0.05" />
        </geometry>
     <material>
        <color rgba="0 0 0 1" />
      </material>
        
    </visual>

  <!-- TODO: Write the visual component for the cylindrical rod (radius=0.01, length=1.) below -->
    <visual>
        <origin xyz = "0 0 -0.5" rpy = "0 0 0" />
        <geometry>
            <cylinder radius="0.01" length="1.0" />
        </geometry>
     <material>
        <color rgba="0 0 0 1" />
      </material>
        
    </visual>
  </link>
"""

double_pendulum_urdf = f"""  
<?xml version="1.0"?><robot name="OurCartPole">
{base_urdf}
{pendulum_link}
{base_joint}
{pendulum_joint}
{second_pendulum_joint}
{second_pendulum_link}
{transmission}
  </robot>
</xml>
"""
print(double_pendulum_urdf)

  
<?xml version="1.0"?><robot name="OurCartPole">

  <link name="base">

    <inertial>
      <origin xyz="0 0 0.25" />
      <mass value="1" />
    </inertial>

    <visual>
      <origin xyz="0 0 0.25" />
      <geometry>
        <box size=".6 .3 .3" />
      </geometry>
      <material>
        <color rgba="0 1 0 1" />
      </material>
    </visual>

    <visual>
      <origin xyz=".15 0 0.025" rpy="0 0 0" />
      <geometry>
        <sphere radius=".05" />
      </geometry>
      <material>
        <color rgba="0 0 0 1" />
      </material>
    </visual>
    
    <visual>
      <origin xyz="-.15 0 0.025" rpy="0 0 0" />
      <geometry>
        <sphere radius=".05" />
      </geometry>
      <material>
        <color rgba="0 0 0 1" />
      </material>
    </visual>
  </link>

 
  <link name="pendulum0">
    
  <!-- This is how you can write comments in urdfs -->
  <!-- TODO: Write the inertial component below -->
    <inertial>
      <origin xyz="0 0 -1.0" rpy="0 0 0" />
      <m

Time to visualize the double-pendulum cart-pole. Its initial configuration should look like in Figure 5. 
<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/double_cart_pole_initial.png" width=600 />
</div>
<div align="center">
Figure 5 : double cart-pole at rest
</div>

Try varying the values for $\theta_0$ and $\theta_1$ to see if they match the definition in Figure 4.


In [24]:
if double_pendulum_urdf != "":
    visualizer = ModelVisualizer(meshcat=meshcat)
    visualizer.parser().AddModelsFromString(double_pendulum_urdf, "urdf")
    visualizer.Run(loop_once=not running_as_notebook)
    meshcat.Delete()
    meshcat.DeleteAddedControls()

INFO:drake:Click 'Stop Running' or press Esc to quit


What is the state at the unstable equilibrium for the double-pendulum cart-pole, when both the pendulums are standing 
upright one over another?
**Note**: The state here is defined by $[x, \theta_0, \theta_1, \dot{x}, \dot{\theta}_0, \dot{\theta}_1]$

In [25]:
x_star_double_pendulum = [0, np.pi, 0, 0, 0, 0]

## LQR for Cart-Poles

Now that we've successfully constructed a URDF file, we can add it to LQR and run our robot! 
Example 3.5 in the textbook will be helpful for building an LQR controller. Read the example carefully and fill in 
the following function.

In [26]:
def cartpole_balancing(cartpole_urdf, x_star, Q, R):
    """
    Arguments:
        cartpole_urdf: str
            a string that contains a urdf description of the system
        x_star: array
            a fixed point of the system; the desired equilibrium point
            we want the system to reach
        Q: state cost matrix in LQR
        R: input cost matrix in LQR

    simulates and generates an animation for the lqr controlled system
    """

    builder = DiagramBuilder()

    cartpole, scene_graph = AddMultibodyPlantSceneGraph(builder, time_step=0.0)
    Parser(cartpole).AddModelsFromString(cartpole_urdf, "urdf")
    cartpole.Finalize()
    cartpole.set_name("cartpole")

    # TODO:
    # 1. obtain the context from the cartpole plant
    context = cartpole.CreateDefaultContext()

    # 2. set the state vector in the context to x_star
    cartpole.SetPositionsAndVelocities(context, x_star) 

    # 3. fix the actuation input port to zero
    cartpole.get_actuation_input_port().FixValue(context, [0])

    # 4. synthesize a LinearQuadraticRegulator, and add it to the builder

    LQRcontroller = LinearQuadraticRegulator(
        cartpole,
        context,
        Q,
        R,
        input_port_index=cartpole.get_actuation_input_port().get_index(),
    )
    
    # 5. wire cart-pole and lqr
    LQR_controller = builder.AddSystem(LQRcontroller)
    builder.Connect(cartpole.get_state_output_port(), LQR_controller.get_input_port(0))
    builder.Connect(LQR_controller.get_output_port(0), cartpole.get_actuation_input_port())
    
    # add a visualizer
    meshcat.Delete()
    visualizer = MeshcatVisualizer.AddToBuilder(builder, scene_graph, meshcat)
    visualizer.set_name("visualizer")

    # finish building the block diagram
    diagram = builder.Build()
    return diagram

In [27]:
def simulate_and_animate(diagram, x0, sim_time=5.0, visualize=True):
    # instantiate a simulator
    simulator = Simulator(diagram)
    simulator.set_publish_every_time_step(False)  # makes sim faster
    simulator.get_mutable_integrator().set_fixed_step_mode(True)

    # start recording the video for the animation of the simulation
    visualizer = diagram.GetSubsystemByName("visualizer")
    visualizer.StartRecording(False)

    if len(x0) != diagram.GetSubsystemByName("cartpole").num_continuous_states():
        print(f"Your plant doesn't have {len(x0)} state variables.")
        return

    # reset initial time and state
    context = simulator.get_mutable_context()
    context.SetTime(0.0)
    context.SetContinuousState(x0)

    # run sim
    simulator.Initialize()
    simulator.AdvanceTo(sim_time)

    # stop video
    visualizer.PublishRecording()
    visualizer.DeleteRecording()

### LQR for single-pendulum cart-pole

In [30]:
# simulate and animate the lqr controller for single-pendulum cart-pole
Q = np.diag((10.0, 10.0, 1.0, 1.0))
R = np.eye(1)
x0 = np.array([0, 0.9 * np.pi, 0, 0])
single_cartpole_diagram = cartpole_balancing(
    single_pendulum_urdf, x_star_single_pendulum, Q, R
)
simulate_and_animate(
    single_cartpole_diagram,
    x0,
    sim_time=5 if running_as_notebook else 0.1,
    visualize=running_as_notebook,
)

### LQR for double-pendulum cart-pole

In [32]:
# simulate and animate the lqr controller for double-pendulum cart-pole
Q = np.diag((10.0, 10.0, 10.0, 1.0, 1.0, 1.0))
R = np.eye(1)
x0 = np.array([-2, 0.9 * np.pi, -0.2, 0, 0, 0])

if double_pendulum_urdf != "":
    double_cartpole_diagram = cartpole_balancing(
        double_pendulum_urdf, x_star_double_pendulum, Q, R
    )
    simulate_and_animate(
        double_cartpole_diagram,
        x0,
        sim_time=10 if running_as_notebook else 0.1,
        visualize=running_as_notebook,
    )

Vary the initial condition x0 further away from the unstable equilibrium. How far you could deviate $\theta_0$ 
and/or $\theta_1$ before balancing fails?

## Summary
`
This notebook is used to demonstrate the use of Drake software on linearization of simple nonlinear dynamics, 
and perform LQR control on the linearized plants. We also address writing URDF to describe some variety of cart pole systems. 
See [ [1](https://underactuated.csail.mit.edu/) ] for more rigorous discussion. 

## Exercises

1. LQR control works when the initial cart-pole configuration does not deviate too much from the unstable equilibrium. 
[Swing-up control](https://underactuated.csail.mit.edu/acrobot.html#section6) may be used to balance the pendulum from 
the rest state. Can you implement it for a single cart-pole? a double cart-pole?

2. Write URDF for an Acrobot in Figure 6 and balance it in the upright position using LQR control.
<div align="center">
<img src="https://raw.githubusercontent.com/dewdotninja/sharing-github/master/acrobot.png" width=500 />
</div>
<div align="center">
Figure 6: an Acrobot
</div>

### Reference

1. Russ Tedrake. Underactuated Robotics: Algorithms for Walking, Running, Swimming, Flying, and Manipulation 
(Course Notes for MIT 6.832).  https://underactuated.csail.mit.edu/